In [1]:
import cadquery as cq
from cadquery import Workplane, Assembly, Location, Vector, Color, exporters
# from cq_server.ui import ui, show_object
# from ocp_vscode import *

from ocp_vscode import show, show_object, reset_show, set_port, set_defaults, get_defaults
set_port(3939)

In [25]:
reset_show()

In [ ]:
import cadquery as cq

# Define a unit for micrometers.
um = 0.001

def build_cell(pad_length, di_thickness):
    """
    Build a single capacitor cell.
    
    Parameters:
      pad_length (float): The length of the pad (formerly c_pad_width) in µm.
      di_thickness (float): The thickness of the dielectric (formerly via_thickness) in µm.
      
    Returns:
      Assembly: A CadQuery Assembly with all parts for the cell.
    """
    # Basic parameters (all dimensions in µm, then scaled by um)
    bar_width      = 300 * um
    bar_length     = 2000 * um
    bar_thickness  = 20 * um
    gap            = 2000 * um

    top_bar_width  = 2300 * um
    top_bar_length = 300 * um

    c_bridge_width = 300 * um
    c_bridge_length= 450 * um

    signal_pad_length = 550 * um

    via_r = c_bridge_width / 2

    # The pad (c_pad) now uses pad_length (in µm)
    cell_wp = cq.Workplane("XY")
    left_bar = cell_wp.rect(bar_width, bar_length, centered=False).extrude(bar_thickness)
    right_bar = cq.Workplane("XY").move(gap, 0).rect(bar_width, bar_length, centered=False).extrude(bar_thickness)
    top_bar = cq.Workplane("XY").moveTo(0,0).move(0,bar_length)\
                 .rect(top_bar_width, top_bar_length, centered=False).extrude(bar_thickness)
    c_bridge = cq.Workplane("XY").move(gap/2, bar_length)\
                   .rect(c_bridge_width, -c_bridge_length, centered=False).extrude(bar_thickness)
    c_pad = cq.Workplane("XY").moveTo(top_bar_width/2, (bar_length - c_bridge_length) - (pad_length*um)/2)\
                 .rect(pad_length*um, pad_length*um, centered=True).extrude(bar_thickness)
    
    bot_ci = left_bar.union(right_bar).union(top_bar).union(c_bridge).union(c_pad)
    
    signal_pad = cq.Workplane("XY").move(gap/2, 0)\
                     .rect(bar_width, signal_pad_length, centered=False).extrude(bar_thickness)
    
    via = cq.Workplane("XY").moveTo(top_bar_width/2, signal_pad_length)\
              .circle(via_r).extrude(di_thickness*um + bar_thickness)
    
    top_electrode = cq.Workplane("XY").workplane(offset=di_thickness*um)\
                        .moveTo(top_bar_width/2, (bar_length - c_bridge_length) - (pad_length*um)/2)\
                        .rect(pad_length*um, pad_length*um, centered=True).extrude(bar_thickness)
    
    top_connector = cq.Workplane("XY").workplane(offset=di_thickness*um)\
                        .moveTo(top_bar_width/2 - c_bridge_width/2, (bar_length - c_bridge_length - pad_length*um))\
                        .rect(c_bridge_width, -(bar_length - c_bridge_length - pad_length*um - signal_pad_length), centered=False)\
                        .extrude(bar_thickness)
    top_ci = top_electrode.union(top_connector)

    # DI: starting at the XY plane. Its reference point is the top-left corner of the pad.
    c_pad_tl = (
        c_pad.faces(">Z")
        .vertices("<X and >Y")
        .val()
        .Center()
    )
    DI = cq.Workplane("XY").moveTo(c_pad_tl.x - 100*um, c_pad_tl.y + 100*um)\
             .rect(pad_length*um + 200*um, -(bar_length - c_bridge_length - bar_width), centered=False)\
             .extrude(di_thickness*um)
    
    # Create an assembly for the cell.
    cell_assy = cq.Assembly()
    cell_assy.add(bot_ci, name="bot_CI",color=Color("gray"))
    cell_assy.add(signal_pad, name="signal_CI",color=Color("gray"))
    cell_assy.add(via, name="via",color=Color("gray"))
    cell_assy.add(top_ci, name="top_connector",color=Color("gray"))
    cell_assy.add(DI, name="DI",color=Color("Quantity_NOC_DARKGOLDENROD2"))
    
    return cell_assy

def build_array():
    """
    Build a 10x10 array of capacitor cells.
    
    - Rows: vary pad_length from 200 to 650 µm (row 0: 200, row 1: 250, …, row 9: 650)
    - Columns: vary di_thickness among: 20, 30, 40, 50, 60, 80, 100, 120, 160, 200 µm.
    
    Returns:
      Assembly: A CadQuery Assembly with the array.
    """
    # Define the parameter lists.
    pad_lengths = [200, 250, 300, 350, 400, 450, 500, 550, 600, 650]  # in µm
    di_thicknesses = [20, 30, 40, 50, 60, 80, 100, 120, 160, 200]       # in µm

    # Choose a spacing that will keep the cells from overlapping.
    # (These values may need to be adjusted depending on your design extents.)
    spacing_x = 3000 * um
    spacing_y = 3000 * um

    array_assy = cq.Assembly()

    for row in range(10):
        for col in range(10):
            cell = build_cell(pad_lengths[row], di_thicknesses[col])
            # Compute the translation for this cell.
            x_offset = col * spacing_x
            y_offset = row * spacing_y
            # Add the cell into the overall assembly.
            array_assy.add(cell, name=f"cell_{row}_{col}", loc=cq.Location(cq.Vector(x_offset, y_offset, 0)))
    
    return array_assy

# Build the 10x10 array and display it.
final_assy = build_array()
show_object(final_assy, name="ArrayAssembly")

# Optionally, you can save the assembly to a STEP file.
final_assy.save("parallel_capacitor_array.step")


cccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccc


In [ ]:
import cadquery as cq
from cadquery import Color

# Define a unit for micrometers.
um = 0.001

def build_cell(pad_length, di_thickness):
    """
    Build a single capacitor cell.
    
    Parameters:
      pad_length (float): The pad length (formerly c_pad_width) in µm.
      di_thickness (float): The dielectric thickness (formerly via_thickness) in µm.
      
    Returns:
      dict: Dictionary containing the six parts as CadQuery solids.
            Keys: "bot_CI", "signal_CI", "via", "top_electrode", "top_connector", "DI".
    """
    # Basic parameters (all dimensions in µm, then scaled by um)
    bar_width      = 300 * um
    bar_length     = 2000 * um
    bar_thickness  = 20 * um
    gap            = 2000 * um

    top_bar_width  = 2300 * um
    top_bar_length = 300 * um

    c_bridge_width = 300 * um
    c_bridge_length= 450 * um

    signal_pad_length = 550 * um

    via_r = c_bridge_width / 2

    # Build the bottom layer (bot_CI)
    wp = cq.Workplane("XY")
    left_bar = wp.rect(bar_width, bar_length, centered=False).extrude(bar_thickness)
    right_bar = cq.Workplane("XY").move(gap, 0).rect(bar_width, bar_length, centered=False).extrude(bar_thickness)
    top_bar = cq.Workplane("XY").moveTo(0, 0).move(0, bar_length)\
                .rect(top_bar_width, top_bar_length, centered=False).extrude(bar_thickness)
    c_bridge = cq.Workplane("XY").move(gap/2, bar_length)\
                 .rect(c_bridge_width, -c_bridge_length, centered=False).extrude(bar_thickness)
    c_pad = cq.Workplane("XY").moveTo(top_bar_width/2, (bar_length - c_bridge_length) - (pad_length*um)/2)\
                 .rect(pad_length*um, pad_length*um, centered=True).extrude(bar_thickness)
    bot_CI = left_bar.union(right_bar).union(top_bar).union(c_bridge).union(c_pad)
    
    # Build the signal pad.
    signal_CI = cq.Workplane("XY").move(gap/2, 0)\
                     .rect(bar_width, signal_pad_length, centered=False).extrude(bar_thickness)
    
    
    # Build the via.
    via = cq.Workplane("XY").moveTo(top_bar_width/2, signal_pad_length)\
              .circle(via_r).extrude(di_thickness*um + bar_thickness)
    
    
    # Build the top electrode.
    top_electrode = cq.Workplane("XY").workplane(offset=di_thickness*um)\
                        .moveTo(top_bar_width/2, (bar_length - c_bridge_length) - (pad_length*um)/2)\
                        .rect(pad_length*um, pad_length*um, centered=True).extrude(bar_thickness)
    
    
    # Build the top connector.
    top_connector = cq.Workplane("XY").workplane(offset=di_thickness*um)\
                        .moveTo(top_bar_width/2 - c_bridge_width/2, (bar_length - c_bridge_length - pad_length*um))\
                        .rect(c_bridge_width, -(bar_length - c_bridge_length - pad_length*um - signal_pad_length), centered=False)\
                        .extrude(bar_thickness)
    top_ci = top_electrode.union(top_connector)
    
    # Build the DI (dielectric island) layer.
    # Its reference point is defined relative to the top-left corner of the pad.
    c_pad_tl = (
        c_pad.faces(">Z")
        .vertices("<X and >Y")
        .val()
        .Center()
    )
    DI = cq.Workplane("XY").moveTo(c_pad_tl.x - 100*um, c_pad_tl.y + 100*um)\
             .rect(pad_length*um + 200*um, -(bar_length - c_bridge_length - bar_width), centered=False)\
             .extrude(di_thickness*um)
    
    
    return {
        "bot_CI": bot_CI,
        "signal_CI": signal_CI,
        "via": via,
        "top_ci": top_ci,
        "DI": DI
    }

def build_array():
    """
    Build a 10x10 array of capacitor cells and organize each layer into its own assembly.
    
    - Rows: vary pad_length from 200 to 650 µm (row 0: 200, row 1: 250, …, row 9: 650)
    - Columns: vary di_thickness among: 20, 30, 40, 50, 60, 80, 100, 120, 160, 200 µm.
    
    Returns:
      Tuple containing:
        - Global assemblies for each layer (bot_CI, signal_CI, via, top_electrode, top_connector, DI)
        - A combined final assembly (which includes all layers)
    """
    # Parameter lists.
    pad_lengths = [200, 250, 300, 350, 400, 450, 500, 550, 600, 650]  # µm
    di_thicknesses = [20, 30, 40, 50, 60, 80, 100, 120, 160, 200]       # µm

    # Set spacing so cells do not overlap.
    spacing_x = 3000 * um
    spacing_y = 3000 * um

    # Global assemblies for each layer.
    assy_bot_CI       = cq.Assembly()
    assy_signal_CI    = cq.Assembly()
    assy_via          = cq.Assembly()
    assy_top_ci       = cq.Assembly()
    assy_DI           = cq.Assembly()
    
    for row in range(10):
        for col in range(10):
            cell_parts = build_cell(pad_lengths[row], di_thicknesses[col])
            # Calculate the cell's placement offset.
            x_offset = col * spacing_x
            y_offset = row * spacing_y
            loc = cq.Location(cq.Vector(x_offset, y_offset, 0))
            # Add each part to its corresponding global assembly.
            assy_bot_CI.add(cell_parts["bot_CI"], name=f"bot_CI_{row}_{col}", loc=loc,color=Color("gray"))
            assy_signal_CI.add(cell_parts["signal_CI"], name=f"signal_CI_{row}_{col}", loc=loc,color=Color("gray"))
            assy_via.add(cell_parts["via"], name=f"via_{row}_{col}", loc=loc,color=Color("gray"))
            assy_top_ci.add(cell_parts["top_ci"], name=f"top_ci_{row}_{col}", loc=loc,color=Color("gray"))
            assy_DI.add(cell_parts["DI"], name=f"DI_{row}_{col}", loc=loc,color=Color("Quantity_NOC_DARKGOLDENROD2"))
    """ assy_DI.color("Quantity_NOC_DARKGOLDENROD2")
    assy_bot_CI.color("gray")
    assy_signal_CI.color("gray")
    assy_via.color("gray")
    assy_top_ci.color("gray") """
    # Combine all layers into one final assembly.
    final_assy = cq.Assembly()
    final_assy.add(assy_bot_CI, name="bot_CI_layer")
    final_assy.add(assy_signal_CI, name="signal_CI_layer")
    final_assy.add(assy_via, name="via_layer")
    final_assy.add(assy_top_ci, name="top_electrode_layer")
    final_assy.add(assy_DI, name="DI_layer")
    
    return (assy_bot_CI, assy_signal_CI, assy_via, assy_top_ci, assy_DI, final_assy)

# Build the assemblies.
assy_bot_CI, assy_signal_CI, assy_via, assy_top_ci, assy_DI, final_assy = build_array()

# Display the final combined assembly.
show_object(final_assy, name="FinalAssembly")
# Export each individual layer to a STEP file.



+ccccccccc+ccccccccc+ccccccccc+ccccccccc+ccccccccc+ccccccccc+ccccccccc+ccccccccc+ccccccccc+ccccccccc+ccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccc++++++++++cccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccc++++++++++++++++++++++++++++++++++++++++++++++++++++++++++++++++++++++++++++++++++++++++++++++++++++++++++++++++++++++++++++++++++++++++++++++++++++++++++++++++++++++++++++++++++++++++++++++++++++++++


In [27]:
import os

# Define the output folder.
output_folder = "c1-output"
os.makedirs(output_folder, exist_ok=True)

# Export each individual layer to a STEP file in the output folder.
assy_bot_CI.save(os.path.join(output_folder, "bot_CI_layer.step"))
assy_signal_CI.save(os.path.join(output_folder, "signal_CI_layer.step"))
assy_via.save(os.path.join(output_folder, "via_layer.step"))
assy_top_ci.save("C1-output\top_ci.step")
assy_DI.save(os.path.join(output_folder, "DI_layer.step"))

# Export the combined final assembly.
final_assy.save(os.path.join(output_folder, "parallel_capacitor_array_combined.step"))